In [1]:
from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

# Imports
import numpy as np
import tensorflow as tf

tf.logging.set_verbosity(tf.logging.INFO)

In [2]:
def cnn_model_fn(features, labels, mode):
  """Model function for CNN."""
  # Input Layer
  input_layer = tf.reshape(features["x"], [-1, 28, 28, 1])

  # Convolutional Layer #1
  conv1 = tf.layers.conv2d(
      inputs=input_layer,
      filters=32,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)

  # Pooling Layer #1
  pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2, 2], strides=2)

  # Convolutional Layer #2 and Pooling Layer #2
  conv2 = tf.layers.conv2d(
      inputs=pool1,
      filters=64,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)
  pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2, 2], strides=2)

  # Dense Layer
  pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64])
  dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)
  dropout = tf.layers.dropout(
      inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)

  # Logits Layer
  logits = tf.layers.dense(inputs=dropout, units=10)

  predictions = {
      # Generate predictions (for PREDICT and EVAL mode)
      "classes": tf.argmax(input=logits, axis=1),
      # Add `softmax_tensor` to the graph. It is used for PREDICT and by the
      # `logging_hook`.
      "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
  }

  if mode == tf.estimator.ModeKeys.PREDICT:
    return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)

  # Calculate Loss (for both TRAIN and EVAL modes)
  loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=logits)

  # Configure the Training Op (for TRAIN mode)
  if mode == tf.estimator.ModeKeys.TRAIN:
    optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
    train_op = optimizer.minimize(
        loss=loss,
        global_step=tf.train.get_global_step())
    return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)

  # Add evaluation metrics (for EVAL mode)
  eval_metric_ops = {
      "accuracy": tf.metrics.accuracy(
          labels=labels, predictions=predictions["classes"])}
  return tf.estimator.EstimatorSpec(
      mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)

In [3]:
# Load training and eval data
mnist = tf.contrib.learn.datasets.load_dataset("mnist")
train_data = mnist.train.images # Returns np.array
train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
eval_data = mnist.test.images # Returns np.array
eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)

Instructions for updating:
Use the retry module or similar alternatives.
Instructions for updating:
Please use tf.data.
Instructions for updating:
Please use alternatives such as official/mnist/dataset.py from tensorflow/models.
Instructions for updating:
Please use alternatives such as official/mnist/dataset.py from tensorflow/models.
Instructions for updating:
Please write your own downloading logic.
Instructions for updating:
Please use urllib or similar directly.
Successfully downloaded train-images-idx3-ubyte.gz 9912422 bytes.
Instructions for updating:
Please use tf.data to implement this functionality.
Extracting MNIST-data/train-images-idx3-ubyte.gz
Successfully downloaded train-labels-idx1-ubyte.gz 28881 bytes.
Instructions for updating:
Please use tf.data to implement this functionality.
Extracting MNIST-data/train-labels-idx1-ubyte.gz
Successfully downloaded t10k-images-idx3-ubyte.gz 1648877 bytes.
Extracting MNIST-data/t10k-images-idx3-ubyte.gz
Successfully downloaded t10k-

In [8]:
# Create the Estimator
mnist_classifier = tf.estimator.Estimator(
  model_fn=cnn_model_fn, model_dir="/tmp/mnist_convnet_model")

# Set up logging for predictions
# Log the values in the "Softmax" tensor with label "probabilities"
tensors_to_log = {"probabilities": "softmax_tensor"}
logging_hook = tf.train.LoggingTensorHook(
  tensors=tensors_to_log, every_n_iter=50)

# Train the model
train_input_fn = tf.estimator.inputs.numpy_input_fn(
  x={"x": train_data},
  y=train_labels,
  batch_size=100,
  num_epochs=None,
  shuffle=True)
mnist_classifier.train(
  input_fn=train_input_fn,
  steps=20000,
  hooks=[logging_hook])

INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_save_checkpoints_secs': 600, '_session_config': None, '_keep_checkpoint_max': 5, '_task_type': 'worker', '_global_id_in_cluster': 0, '_is_chief': True, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x1a1f24d850>, '_evaluation_master': '', '_save_checkpoints_steps': None, '_keep_checkpoint_every_n_hours': 10000, '_service': None, '_num_ps_replicas': 0, '_tf_random_seed': None, '_master': '', '_num_worker_replicas': 1, '_task_id': 0, '_log_step_count_steps': 100, '_model_dir': '/tmp/mnist_convnet_model', '_save_summary_steps': 100}
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/mnist_convnet_model/model.ckpt-20000
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Saving checkpoints for 2

INFO:tensorflow:loss = 0.22498553, step = 20001
INFO:tensorflow:probabilities = [[0.9998696  0.00000011 0.00000893 0.000002   0.00000112 0.00000517
  0.00009462 0.000013   0.00000189 0.00000361]
 [0.         0.00000006 0.99999523 0.00000459 0.00000001 0.
  0.         0.         0.00000017 0.        ]
 [0.00001012 0.00000028 0.00092417 0.9986992  0.00000034 0.00013936
  0.00000001 0.00000022 0.00008489 0.00014127]
 [0.99953115 0.         0.0003964  0.00001581 0.00000003 0.00004949
  0.00000004 0.00000066 0.00000017 0.00000631]
 [0.00001176 0.0000137  0.0000023  0.00008432 0.00002728 0.9982672
  0.00004571 0.00009886 0.0014414  0.00000758]
 [0.00022429 0.00121481 0.00033009 0.00147916 0.00039342 0.991043
  0.00021285 0.00063656 0.00420102 0.00026489]
 [0.00004433 0.00013802 0.00001661 0.00130273 0.01694039 0.00213281
  0.00000503 0.00388858 0.00013281 0.97539866]
 [0.9994393  0.00000001 0.00024085 0.00001911 0.         0.00003684
  0.         0.00011086 0.00001147 0.00014146]
 [0.0000001

INFO:tensorflow:global_step/sec: 8.95911
INFO:tensorflow:probabilities = [[0.00059186 0.00349679 0.86791074 0.00246746 0.00268587 0.0000116
  0.00003154 0.11494862 0.00520064 0.00265491]
 [0.00014161 0.00001126 0.0000147  0.00000889 0.00003828 0.99845386
  0.00007849 0.00001508 0.00123206 0.00000583]
 [0.00000618 0.00000044 0.0000032  0.00046173 0.00000036 0.9995029
  0.00000086 0.00000004 0.00000086 0.00002336]
 [0.00016555 0.00000576 0.00113218 0.00013835 0.00015885 0.00001065
  0.00004797 0.00001483 0.9980965  0.00022941]
 [0.00000478 0.00014904 0.00000588 0.00002308 0.8283899  0.00010982
  0.00008    0.00085555 0.00203809 0.16834384]
 [0.0000203  0.9936784  0.0004622  0.00339151 0.00007842 0.00003602
  0.0001195  0.00116828 0.00048792 0.00055743]
 [0.00000088 0.00000005 0.00000082 0.00000245 0.999047   0.00004194
  0.00001841 0.0001729  0.00006614 0.00064953]
 [0.00027081 0.00021719 0.00021401 0.01070179 0.00001295 0.929767
  0.00005802 0.00004607 0.05816774 0.00054436]
 [0.0000001

INFO:tensorflow:loss = 0.0681328, step = 20101 (11.165 sec)
INFO:tensorflow:probabilities = [[0.02250721 0.00001255 0.00042577 0.01695064 0.00000117 0.9551794
  0.00001747 0.00015178 0.00419872 0.00055537]
 [0.00000339 0.00001783 0.00008533 0.00000988 0.00000014 0.00000005
  0.         0.9997708  0.00000069 0.00011197]
 [0.00560333 0.0000582  0.00162514 0.01012207 0.00178822 0.00139321
  0.00253539 0.00053365 0.79263955 0.18370119]
 [0.00000279 0.99676514 0.00005044 0.00252018 0.00007387 0.00005052
  0.00003298 0.00006414 0.00036717 0.0000728 ]
 [0.00003931 0.00433803 0.00014296 0.03327644 0.00022904 0.87690413
  0.00006101 0.00014744 0.03946817 0.04539354]
 [0.00009098 0.00000809 0.00022558 0.00003234 0.00052408 0.00021078
  0.99878615 0.00000219 0.000086   0.00003375]
 [0.00000118 0.00000073 0.00000534 0.00028533 0.00567547 0.0000132
  0.00000053 0.00165003 0.00007503 0.99229324]
 [0.00194714 0.00047741 0.98641765 0.00052449 0.0002213  0.00001103
  0.00015145 0.00007793 0.00983928 0.

INFO:tensorflow:global_step/sec: 9.30257
INFO:tensorflow:probabilities = [[0.00001627 0.0000001  0.00000006 0.01318401 0.00000005 0.98629236
  0.         0.00000336 0.00016582 0.00033801]
 [0.998965   0.00000081 0.00004462 0.00004143 0.00000115 0.00006498
  0.00002397 0.0002568  0.00003175 0.00056938]
 [0.         0.00000001 0.00000786 0.9999912  0.         0.00000094
  0.         0.         0.00000003 0.00000003]
 [0.00448212 0.00000279 0.00002339 0.00055955 0.00003444 0.9210296
  0.00000616 0.06952731 0.00247473 0.00185997]
 [0.00399944 0.28045493 0.01253143 0.03125126 0.00674973 0.33331743
  0.2943386  0.00093017 0.03416461 0.00226232]
 [0.00000774 0.00290921 0.9680083  0.02485769 0.00000661 0.00112647
  0.00010105 0.00196008 0.00102051 0.00000237]
 [0.00111156 0.0000155  0.00033797 0.00165127 0.00000851 0.00012825
  0.00000582 0.00000974 0.99671423 0.00001708]
 [0.0003398  0.11817875 0.02344521 0.14641157 0.000161   0.00108628
  0.00033566 0.00135203 0.70847493 0.00021489]
 [0.0000

...

INFO:tensorflow:global_step/sec: 9.27044
INFO:tensorflow:probabilities = [[0.00023263 0.0000173  0.00027816 0.10509638 0.0000138  0.89327663
  0.00003515 0.00000336 0.00090766 0.00013895]
 [0.00006746 0.00004164 0.00017164 0.9911431  0.00000117 0.00855242
  0.00000334 0.00000052 0.00001409 0.00000464]
 [0.01422446 0.08953808 0.86187917 0.00105206 0.00000793 0.0006869
  0.02856105 0.0000027  0.00404756 0.00000005]
 [0.00000475 0.00100351 0.99149525 0.00173904 0.00000288 0.0000042
  0.00000117 0.00439909 0.00128324 0.00006674]
 [0.00000353 0.00000355 0.00006745 0.00006193 0.00000013 0.00000012
  0.         0.9997768  0.00003023 0.00005616]
 [0.9950387  0.00002963 0.00115611 0.0002501  0.00038763 0.0004147
  0.00016207 0.00154682 0.00088913 0.00012504]
 [0.00000037 0.00000002 0.00000277 0.         0.00008876 0.00000139
  0.9999019  0.00000001 0.00000471 0.00000002]
 [0.00000517 0.00000096 0.00010637 0.02104594 0.00113133 0.01651183
  0.00000889 0.01256949 0.00044119 0.9481788 ]
 [0.000003

INFO:tensorflow:loss = 0.1434595, step = 39801 (10.787 sec)
INFO:tensorflow:probabilities = [[0.999798   0.00000008 0.00018849 0.00000009 0.0000001  0.00000062
  0.00000061 0.00000877 0.         0.00000325]
 [0.0000001  0.00000337 0.00000106 0.99788517 0.         0.00203826
  0.00000005 0.         0.00007078 0.00000122]
 [0.99887973 0.00001687 0.00015171 0.00003558 0.00000363 0.00001749
  0.00088463 0.00000141 0.00000884 0.00000026]
 [0.00000125 0.00000422 0.00002908 0.00016465 0.00000052 0.00000167
  0.         0.9997061  0.00002255 0.00006991]
 [0.00030863 0.00000945 0.00274634 0.00012824 0.00000015 0.00000566
  0.00000014 0.00000011 0.9968008  0.00000044]
 [0.00000109 0.         0.00000079 0.00061623 0.00001359 0.00008268
  0.00000001 0.0028231  0.00101165 0.9954509 ]
 [0.00002664 0.00477597 0.00014838 0.00361398 0.0002668  0.00002529
  0.00000023 0.98931247 0.00043844 0.0013918 ]
 [0.00057177 0.00000004 0.00002612 0.00005136 0.00000032 0.00000099
  0.         0.9982552  0.00003694 

INFO:tensorflow:global_step/sec: 8.96857
INFO:tensorflow:probabilities = [[0.00000166 0.00001288 0.00000839 0.0000172  0.00002857 0.00000211
  0.00000016 0.9997906  0.00000541 0.00013308]
 [0.00000599 0.00000698 0.00019193 0.00005863 0.00003833 0.00000524
  0.00000004 0.995346   0.00000161 0.00434528]
 [0.9998596  0.         0.00008077 0.00000001 0.00000132 0.00000141
  0.0000206  0.00000254 0.00000005 0.00003379]
 [0.000203   0.00034593 0.9241459  0.00617421 0.03891115 0.00083271
  0.00021199 0.02915555 0.00000948 0.0000101 ]
 [0.00001768 0.00000874 0.00774712 0.99057543 0.00001516 0.00005971
  0.00007682 0.00000446 0.00149465 0.00000009]
 [0.0000077  0.00000185 0.00008374 0.00008245 0.03585545 0.00000287
  0.00000255 0.0052685  0.00016243 0.9585324 ]
 [0.00001443 0.00001865 0.00000127 0.00076803 0.01735619 0.00321632
  0.00000057 0.00433982 0.00022204 0.97406274]
 [0.0000009  0.9737458  0.00030686 0.00000328 0.00014362 0.00000009
  0.00000026 0.02539372 0.00002486 0.00038051]
 [0.000

INFO:tensorflow:loss = 0.03947744, step = 39901 (11.150 sec)
INFO:tensorflow:probabilities = [[0.00027153 0.00031712 0.00014747 0.09344994 0.00000027 0.00118691
  0.00000013 0.00012215 0.9025523  0.00195214]
 [0.00000047 0.00000009 0.00021001 0.00012407 0.00000001 0.00000002
  0.         0.9996624  0.00000075 0.00000222]
 [0.00000001 0.         0.00000003 0.0000041  0.00002904 0.00000535
  0.         0.0004164  0.00000013 0.9995449 ]
 [0.00000199 0.00001824 0.00006867 0.07058307 0.         0.92103124
  0.         0.00013953 0.00010911 0.00804813]
 [0.00000003 0.00000162 0.00008302 0.00011447 0.00001281 0.00000011
  0.         0.9997763  0.00000488 0.00000684]
 [0.99979275 0.00000016 0.00009166 0.00000028 0.00000668 0.00001377
  0.00005846 0.0000335  0.00000078 0.00000191]
 [0.00001461 0.00001759 0.02094018 0.97767305 0.         0.00000618
  0.         0.00000024 0.0013002  0.00004788]
 [0.00000457 0.00001296 0.00000364 0.00072957 0.00358074 0.00000702
  0.00000035 0.00157632 0.0025812 

INFO:tensorflow:Saving checkpoints for 40000 into /tmp/mnist_convnet_model/model.ckpt.
INFO:tensorflow:Loss for final step: 0.10561899.
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Starting evaluation at 2018-04-06-08:17:49
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/mnist_convnet_model/model.ckpt-40000
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Finished evaluation at 2018-04-06-08:17:53
INFO:tensorflow:Saving dict for global step 40000: accuracy = 0.98, global_step = 40000, loss = 0.06126347
{'loss': 0.06126347, 'global_step': 40000, 'accuracy': 0.98}


In [10]:
# Evaluate the model and print results
eval_input_fn = tf.estimator.inputs.numpy_input_fn(
  x={"x": eval_data},
  y=eval_labels,
  num_epochs=1,
  shuffle=False)
eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
print(eval_results)

INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Starting evaluation at 2018-04-06-08:28:13
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/mnist_convnet_model/model.ckpt-40000
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Finished evaluation at 2018-04-06-08:28:16
INFO:tensorflow:Saving dict for global step 40000: accuracy = 0.98, global_step = 40000, loss = 0.06126347
{'loss': 0.06126347, 'global_step': 40000, 'accuracy': 0.98}


In [15]:
print(mnist)
print(mnist.train.images)
print(mnist.train.labels)
print(np.asarray(mnist.train.labels, dtype=np.int32))

Datasets(train=<tensorflow.contrib.learn.python.learn.datasets.mnist.DataSet object at 0x10cf4c250>, validation=<tensorflow.contrib.learn.python.learn.datasets.mnist.DataSet object at 0x10d09b690>, test=<tensorflow.contrib.learn.python.learn.datasets.mnist.DataSet object at 0x10d09b810>)
[[0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 ...
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]]
[7 3 4 ... 5 6 8]
[7 3 4 ... 5 6 8]
